In [1]:
%pip install pandas pyarrow
%pip install tqdm
%pip install plotly
%pip install nbformat
%pip install ipywidgets
%pip install numba


[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.

[notice] A new release of pip is available: 25.0.1 -> 25.2
[notice] To update, run: pip install --upgrade pip
Note

In [2]:
# function to download data.

import requests
from tqdm import tqdm

def get_filename(ticker, interval, year):
    return f'{ticker}_{interval}_{year}.parquet'

def download(ticker, interval, year):
    filename = get_filename(ticker, interval, year)
    if year:
      # url for seconds
      url = f"https://barsv.com/api/download/file/{ticker}/{year}?format=parquet&interval={interval}"
    else:
      # url for minutes+
      url = f"https://barsv.com/api/download/file/{ticker}/{ticker}_{interval}?interval={interval}&format=parquet"
    response = requests.get(url, stream=True)

    # Get the total file size from the content-length header
    total_size = int(response.headers.get('content-length', 0))

    with open(filename, 'wb') as f, tqdm(
        desc=filename,
        total=total_size,
        unit='iB',
        unit_scale=True,
        unit_divisor=1024,
    ) as bar:
        for data in response.iter_content(chunk_size=1024):
            size = f.write(data)
            bar.update(size)

In [3]:
ticker = 'AAPL'
interval = '5s'
year = '2024'

In [4]:
# download(ticker, interval, year)

In [5]:
# plot last points.
import pandas as pd
import plotly.express as px

filename = get_filename(ticker, interval, year)
df = pd.read_parquet(filename)

fig = px.line(df[-1000:], y='open', title=f'{ticker} Open Prices')
fig.show()

In [6]:
total_bars = df.shape[0]
print(f'Total bars: {total_bars} ({total_bars:,})')

Total bars: 1428355 (1,428,355)


In [ ]:
# Set trailing stop-loos levels
import numpy as np

stop_loss_percents = np.concatenate((np.arange(-0.4, 0, 0.04), np.arange(0.04, 0.44, 0.04)))
stop_loss_levels = stop_loss_percents / 100

print("Уровни стоп-лосса (в процентах):")
print(stop_loss_percents)
print("\nУровни стоп-лосса (в долях):")
print(stop_loss_levels)

Уровни стоп-лосса (в процентах):
[-0.4  -0.36 -0.32 -0.28 -0.24 -0.2  -0.16 -0.12 -0.08 -0.04  0.04  0.08
  0.12  0.16  0.2   0.24  0.28  0.32  0.36  0.4 ]

Уровни стоп-лосса (в долях):
[-0.004  -0.0036 -0.0032 -0.0028 -0.0024 -0.002  -0.0016 -0.0012 -0.0008
 -0.0004  0.0004  0.0008  0.0012  0.0016  0.002   0.0024  0.0028  0.0032
  0.0036  0.004 ]


In [20]:
import numba

@numba.jit(nopython=True)
def calculate_pl_numba(df_open, df_low, df_high, df_close, stop_loss_levels):
    """
    Оптимизированная с помощью Numba функция для расчета P/L со скользящим стоп-лоссом.
    """
    num_entries = len(df_open)
    num_sl_levels = len(stop_loss_levels)
    # Numba плохо работает с list-of-dicts, поэтому будем собирать результаты в NumPy массив
    results_np = np.empty(( (num_entries - 1) * num_sl_levels, 4)) # index, sl_level, profit, entry_price
    result_idx = 0

    # Итерация по каждой точке в экспериментальном датафрейме (кроме последней)
    for i in range(num_entries - 1):
        entry_price = df_open[i]

        # Итерация по каждому уровню стоп-лосса
        for sl_idx in range(num_sl_levels):
            sl_level = stop_loss_levels[sl_idx]
            if sl_level == 0:
                continue

            stop_price = entry_price * (1 + sl_level)
            exit_price = 0.0
            trade_closed = False

            # Поиск момента срабатывания стоп-лосса в будущем
            for j in range(i + 1, num_entries):
                future_low = df_low[j]
                future_high = df_high[j]

                # Для длинных позиций (sl_level < 0)
                if sl_level < 0:
                    if future_low <= stop_price:
                        exit_price = stop_price
                        trade_closed = True
                        break
                    else:
                        new_stop_price = future_high * (1 + sl_level)
                        if new_stop_price > stop_price:
                            stop_price = new_stop_price
                # Для коротких позиций (sl_level > 0)
                elif sl_level > 0:
                    if future_high >= stop_price:
                        exit_price = stop_price
                        trade_closed = True
                        break
                    else:
                        new_stop_price = future_low * (1 + sl_level)
                        if new_stop_price < stop_price:
                            stop_price = new_stop_price

            if not trade_closed:
                exit_price = df_close[-1]

            profit = 0.0
            if sl_level < 0:
                profit = (exit_price - entry_price) / entry_price
            elif sl_level > 0:
                profit = (entry_price - exit_price) / entry_price

            results_np[result_idx, 0] = i
            results_np[result_idx, 1] = sl_level
            results_np[result_idx, 2] = profit
            results_np[result_idx, 3] = entry_price

            result_idx += 1

    return results_np[:result_idx] # Возвращаем только заполненную часть массива

def calculate_pl(df_exp):
    # Подготовим данные для Numba (она лучше работает с NumPy-массивами, чем с Pandas Series)
    df_open_np = df_exp['open'].to_numpy()
    df_low_np = df_exp['low'].to_numpy()
    df_high_np = df_exp['high'].to_numpy()
    df_close_np = df_exp['close'].to_numpy()

    numba_results_np = calculate_pl_numba(df_open_np, df_low_np, df_high_np, df_close_np, stop_loss_levels)

    # Преобразуем результат обратно в DataFrame
    results_df = pd.DataFrame(numba_results_np, columns=['index', 'sl_level', 'profit', 'entry_price'])
    # Конвертируем 'index' в int для корректного использования в качестве индекса
    results_df['index'] = results_df['index'].astype(int)
    return results_df


In [25]:
shift = -40
window = 10
df_exp = df[shift*1000:(shift + window)*1000].copy()
results_df = calculate_pl(df_exp)

In [26]:
# Шаг 4: Визуализация результатов
import plotly.graph_objects as go

fig = go.Figure()

# Добавляем точки стоп-лоссов
# Для лучшей производительности мы можем добавить все точки одним вызовом
# Отфильтруем нулевые SL, так как они не несут информации
plot_df = results_df#[results_df['sl_level'] != 0].copy()
plot_df['sl_price'] = plot_df['entry_price'] * (1 + plot_df['sl_level'])

fig.add_trace(go.Scatter(
    x=plot_df['index'],
    y=plot_df['sl_price'],
    mode='markers',
    marker=dict(
        size=3,
        color=plot_df['profit'],
        colorscale='RdBu', # Red-Blue colorscale, хорошо подходит для профита/убытка
        showscale=True,
        colorbar=dict(title='Profit'),
        cmin=-0.009, # Зададим пределы для цветовой шкалы для наглядности
        cmax=0.009
    )
))

# add ohl prices on top
fig.add_trace(go.Scatter(
    #x=df_exp['timestamp'],
    y=df_exp['open'],
    mode='lines',
    line=dict(color='black', width=1)
))
fig.add_trace(go.Scatter(
    y=df_exp['high'],
    mode='lines',
    line=dict(color='black', width=1)
))
fig.add_trace(go.Scatter(
    y=df_exp['low'],
    mode='lines',
    line=dict(color='black', width=1)
))

fig.update_layout(
    title="Trailing SL profits",
    showlegend=False
)

fig.show()